In [55]:
import warnings
import itertools
import pandas
import math
import sys
import os
import numpy as np
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

In [56]:
# Add detector summary file to check scores for a given profile (Note that if there are missing fields in the file)

detector_summary_file = "../results/my/my_standard_scores.csv"
#colomn name of the profile score in result files
detector_profile = "S(t)_standard"

In [57]:
#Reading summary
Error = None
if os.path.isfile(detector_summary_file):
    summaryDataFrame = pandas.read_csv(detector_summary_file,index_col="File")
    if 'Score' in summaryDataFrame.columns:
        summaryDataFrame = summaryDataFrame.sort_values(by=['Score'],ascending=False)
        print("Printing scores for selected profile (NaN represents total score):")
        print(summaryDataFrame.loc[:, 'Score'])
    else:
        Error = "'Score' colomn mission in data file"
        print(Error)
else:
    Error = "No such file : "+detector_summary_file
    print(Error)

Printing scores for selected profile (NaN represents total score):
File
realKnownCause/nyc_diff.csv   -0.303421
NaN                           -0.303421
Name: Score, dtype: float64


In [58]:
# select detector summary file row(data file name) from above
detector_summary_row = "realKnownCause/nyc_taxi.csv"

# Add detector result file(a single file for specific data file)
result_file = "../results/my/realKnownCause/my_nyc_diff.csv"

In [59]:
if not summaryDataFrame.index.contains(detector_summary_row):
    Error = "No detector_summary_row '"+detector_summary_row+"' in file "+detector_summary_file
else:
    Error = None

if set(['Threshold','TP','TN','FP','FN','Total_Count']).issubset(summaryDataFrame.columns) and Error is None:
    if summaryDataFrame["Threshold"][detector_summary_row].size == 1:
        threshold = summaryDataFrame["Threshold"][detector_summary_row]
        TP = summaryDataFrame["TP"][detector_summary_row]
        TN = summaryDataFrame["TN"][detector_summary_row]
        FP = summaryDataFrame["FP"][detector_summary_row]
        FN = summaryDataFrame["FN"][detector_summary_row]
        total_Count = summaryDataFrame["Total_Count"][detector_summary_row]
    else:
        threshold = summaryDataFrame["Threshold"][detector_summary_row][0]
        TP = summaryDataFrame["TP"][detector_summary_row][0]
        TN = summaryDataFrame["TN"][detector_summary_row][0]
        FP = summaryDataFrame["FP"][detector_summary_row][0]
        FN = summaryDataFrame["FN"][detector_summary_row][0]
        total_Count = summaryDataFrame["Total_Count"][detector_summary_row][0]
else:
    if Error is None:
        Error = "Missing colomns in file "+detector_summary_file
    print(Error)
    print("Run from beginng to clear Error")

No detector_summary_row 'realKnownCause/nyc_taxi.csv' in file ../results/my/my_standard_scores.csv
Run from beginng to clear Error


In [60]:
#Ploting Result (Note if the plot is not visible please close the tab shutdown notebook and restart)
#Reading results file 
if os.path.isfile(result_file):
    dataframe = pandas.read_csv(result_file)
    Error = None
else:
    Error = "No such file : "+result_file
    print(Error)

if set(['timestamp','value','anomaly_score','label', detector_profile]).issubset(dataframe.columns)\
        and Error is None:
    x = np.array(dataframe['timestamp'])
    value = np.array(dataframe['value'])
    anomaly_score = np.array(dataframe['anomaly_score'])
    anomaly_label = np.array(dataframe['label'])

    standard_score = np.array(dataframe[detector_profile])
else:
    if Error is None:
        Error = "Missing colomns in file "+result_file
    print(Error)
# Plot values, anomaly score and label scaled to values

if Error is None:
    value_max = np.max(value)
    trace_value = {"x": x,
             "y": value,
             "mode": 'lines',
             "name": 'Value'}

    trace_anomaly_score = {"x": x,
                  "y": anomaly_score*value_max,
                  "mode": 'lines',
                  "name": 'Anomaly score'}

    trace_anomaly_label = {"x": x,
                  "y": anomaly_label*value_max,
                  "mode": 'lines',
                  "name": 'Anomaly window'}
    trace_threshold = {"x": x,
                  "y": np.ones(len(x))*threshold*value_max,
                  "mode": 'lines',
                  "name": 'Anomaly threshold'}

    traces = [trace_value,trace_anomaly_score,trace_threshold,trace_anomaly_label]
    layout = dict(title = "Scalled anomaly score with value : "+result_file,
                  xaxis = dict(title = 'X'),
                  yaxis = dict(title = 'Value')
                 )
    fig = dict(data=traces, layout=layout)
    iplot(fig)

    #plot, anomalys score, label, and result from benchmark
    trace_anomaly_score = {"x": x,
                  "y": anomaly_score,
                  "mode": 'lines',
                  "name": 'Anomaly score'}

    trace_anomaly_label = {"x": x,
                  "y": anomaly_label,
                  "mode": 'lines',
                  "name": 'Anomaly window'}

    trace_threshold = {"x": x,
                  "y": np.ones(len(x))*threshold,
                  "mode": 'lines',
                  "name": 'Anomaly threshold'}

    trace_standard_score = {"x": x,
                  "y": standard_score,
                  "mode": 'lines',
                  "name": 'standard_score'}

    traces = [trace_anomaly_score,trace_threshold,trace_anomaly_label,trace_standard_score]
    layout = dict(title = "Anomaly score : "+result_file,
                  xaxis = dict(title = 'X'),
                  yaxis = dict(title = 'Value')
                 )
    fig = dict(data=traces, layout=layout)
    iplot(fig)
else:
    print(Error)
    print("Run from beginng to clear Error")

In [61]:
if Error is None:
    TP,TN,FP,FN = 0,0,0,0
    for x in standard_score:
        if x > 0:
            TP +=1
        elif x == 0:
            TN +=1
        elif x == -0.11:
            FP +=1
        elif x == -1:
            FN +=1
        else:
            print(x)
    print("For result file : " + result_file)
    print("True Positive (Detected anomalies) : " + str(TP))
    print("True Negative (Detected non anomalies) : " + str(TN))
    print("False Positive (False alarms) : " + str(FP))
    print("False Negative (Anomaly not detected) : " + str(FN))
    print("Total data points : " + str(total_Count))
    print(detector_profile+" score : "+str(np.sum(standard_score)))
else:
    print(Error)
    print("Run from beginng to clear Error")

-0.001334885922682786
-0.0026693787362336275
-0.004003085794449461
-0.005335615375826842
-0.006666577143021998
-0.007995582598856594
-0.009322245537741393
-0.01064618249140848
-0.011967013167868131
-0.013284360882533944
-0.014597852980493578
-0.015907121248939244
-0.017211802318813176
-0.01851153805476769
-0.01980597593258737
-0.02109476940327206
-0.02237757824303244
-0.023654068888506432
-0.02492391475656264
-0.02618679654811635
-0.02744240253544552
-0.02869042883255578
-0.029930579648206564
-0.031162567521273207
-0.03238611353818422
-0.03360094753223415
-0.03480680826463599
-0.03600344358723803
-0.03719061058688962
-0.03836807571149931
-0.03953561487788598
-0.04069301356157745
-0.04184006686876443
-0.042976579590667585
-0.044102366240623365
-0.04521725107423875
-0.04632106809300774
-0.0474136610318208
-0.04849488333083564
-0.04956459809220951
-0.050622678022224095
-0.05166900535936022
-0.05270347178890344
-0.05372597834468183
-0.054736435298554896
-0.05573476203828656
-0.056720886934

-0.0026693787362336275
-0.004003085794449461
-0.005335615375826842
-0.006666577143021998
-0.007995582598856594
-0.009322245537741393
-0.01064618249140848
-0.011967013167868131
-0.013284360882533944
-0.014597852980493578
-0.015907121248939244
-0.017211802318813176
-0.01851153805476769
-0.01980597593258737
-0.02109476940327206
-0.02237757824303244
-0.023654068888506432
-0.02492391475656264
-0.02618679654811635
-0.02744240253544552
-0.02869042883255578
-0.029930579648206564
-0.031162567521273207
-0.03238611353818422
-0.03360094753223415
-0.03480680826463599
-0.03600344358723803
-0.03719061058688962
-0.03836807571149931
-0.03953561487788598
-0.04069301356157745
-0.04184006686876443
-0.042976579590667585
-0.044102366240623365
-0.04521725107423875
-0.04632106809300774
-0.0474136610318208
-0.04849488333083564
-0.04956459809220951
-0.050622678022224095
-0.05166900535936022
-0.05270347178890344
-0.05372597834468183
-0.054736435298554896
-0.05573476203828656
-0.0567208869344466
-0.05769474719699